<a href="https://colab.research.google.com/github/psygorozco/ML/blob/main/LANGCHAIN/Sistema_de_Respuesta_a_Preguntas_simple.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

* Cargar los datos de los "documentos largos".
* Dividir los documentos en secciones cortas llamadas fragmentos (chunks).
* Transformar los fragmentos en vectores númericos (Embeddings)
* Guardar los embeddings en una base de datos vectorial (Pinecone)
* Realizar las consultas

### Preparando los Datos

In [7]:
! pip install -r ./requirements.txt -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 262.4/262.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 809.1/809.1 kB 10.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 14.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.0/211.0 kB 17.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 7.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 19.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 260.9/260.9 kB 22.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.9/70.9 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 2.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.8/77.8 kB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 5.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.0/53.0 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━

In [8]:
! pip install pypdf -q

In [9]:
! pip install docx2txt -q

In [5]:
! pip install wikipedia -q

  Preparing metadata (setup.py) ... done


In [10]:
import os
from dotenv import load_dotenv, find_dotenv

In [11]:
load_dotenv(find_dotenv(), override=True)

True

### Cargar Documentos

In [12]:
def cargar_documento(archivo):
    import os
    nombre, extension = os.path.splitext(archivo)
    if extension == '.pdf':
        from langchain.document_loaders import PyPDFLoader
        print(f'Cargando {archivo}...')
        loader = PyPDFLoader(archivo)
    elif extension == '.docx':
        from langchain.document_loaders import Docx2txtLoader
        print(f'Cargando {archivo}...')
        loader = Docx2txtLoader(archivo)
    else:
        print('El formato del documento no está soportado!')
        return None

    data = loader.load()
    return data

In [13]:
documento = "Minecraft.pdf"
contenido = cargar_documento(documento)
print(contenido)

Cargando Minecraft.pdf...
[Document(page_content='Minecraft  \n \nMinecraft  es un  videojuego  de construcción de tipo «mundo abierto » o sandbox  creado \noriginalmente  por el sueco  Markus Persson  (conocido comúnmente como «Notch») ,19 y \nposteriormente desarrollado por  Mojang Studios  (actualmente parte de  Microsoft ).20 Fue \nlanzado el 17 de mayo de 2009, y después de numerosos cam bios, su primera versión estable \n«1.0» fue publicada el 18 de noviembre de 2011.  \nMarkus Persson , el creador de Minecraft . \nUn mes antes del lanzamiento de su versión completa se estrenó una versión para \ndispositivos móviles llamada  Minecraft: Pocket Edition  en Android ,21 y el 17 de noviembre del \nmismo año fue lanzada la misma versión para  iOS.22 El 9 de mayo de 2012 fue lanzada la \nversión del  juego para  Xbox 360  y PS3. Todas las versiones de Minecraft  reciben \nactualizaciones constantes desde su lanzamiento. En octubre de 2014,  Minecraft  lanzó su \nedición para  PlayStatio

In [14]:
print(len(contenido))

7


### Fragmentar los datos

In [15]:
def fragmentar(data):
    from langchain.text_splitter import RecursiveCharacterTextSplitter
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=150, chunk_overlap=20)
    fragmentos = text_splitter.split_documents(data)
    return fragmentos

In [16]:
fragmentos = fragmentar(contenido)
print(len(fragmentos))

209


In [17]:
fragmentos[2]

Document(page_content='posteriormente desarrollado por  Mojang Studios  (actualmente parte de  Microsoft ).20 Fue', metadata={'source': 'Minecraft.pdf', 'page': 0})

### Costos OpenAI

In [18]:
def costo_embedding(texts):
    import tiktoken
    enc = tiktoken.encoding_for_model('text-embedding-ada-002')
    total_tokens = sum([len(enc.encode(page.page_content)) for page in texts])
    print(f'Total Tokens: {total_tokens}')
    print(f'Embedding Cost in USD: {total_tokens / 1000000 * 0.10:.5f}')

In [19]:
costo_embedding(fragmentos)

Total Tokens: 5264
Embedding Cost in USD: 0.00053


crear los embeddings

In [21]:
from langchain.embeddings.openai import OpenAIEmbeddings
embeddings = OpenAIEmbeddings()

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.0.9 and will be removed in 0.2.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import OpenAIEmbeddings`.
  warn_deprecated(


In [ ]:
vectores = embeddings.embed_query(fragmentos[1].page_content)
print(vectores)

In [23]:
print(vectores)

[-0.003746347973088681, -0.01711652802978068, 0.01993556137357913, -0.010986140014125305, 0.011788688617538364, 0.0159295667198995, -0.04418734840148277, -0.0301326420604821, -0.02017834971856069, -0.012031476031197346, 0.009704761221489645, 0.016118401685408453, 0.0022255533873497906, -0.0024025859346837922, 0.003746347973088681, 0.019868120580560953, -0.025762464889330136, 0.013387040254946544, 0.008720122290662994, -0.02036718468406964, -0.0318051800603264, 0.02549270171725743, 0.0031494952319310525, -0.0012830651849901435, -0.01060847101442997, 0.0004493257153920619, 0.022822037373040907, -0.03474560757661562, -8.930664639188587e-05, -0.003581117611098989, -0.001364837402638391, 0.0016042529629109786, 0.007121770653254814, -0.013548898530719198, -0.047505445848789914, -0.0009087675730199148, -0.015470967650995262, -0.03547396888626999, 0.016469094926690065, -0.01460772289265939, 0.007458975549668273, 0.0039115785679090164, 0.01374447720300094, -0.028109412682001348, -0.027151750440

In [38]:
for i, fragmento in enumerate(fragmentos):
    # Obtener los vectores de embeddings del fragmento
    vectores = embeddings.embed_query(fragmento.page_content)

    # Imprimir el fragmento y sus vectores
    print(f"Fragmento {i + 1}:")
    print("Texto del fragmento:", fragmento.page_content)
    print("Vectores de embeddings:", vectores)
    print()

Fragmento 1:
Texto del fragmento: Minecraft  
 
Minecraft  es un  videojuego  de construcción de tipo «mundo abierto » o sandbox  creado
Vectores de embeddings: [-0.010625903903452454, -0.04213652549367681, 0.0003574607100023141, -0.030075044596902585, -0.00037856011478026185, 0.011812386557416763, -0.027662747672489652, -0.02768896812926412, 0.011779610520787371, -0.030206146880774932, 0.01355605717746768, 0.006928797146509648, 0.014788426096448615, -0.004624660770444664, 0.015181735742033483, 0.0032284130653006857, -0.016571427401661235, -0.005575157916454835, 0.015758589516362248, -0.016532097647822142, -0.02753164538861731, 0.01956057810040293, -0.0016305944345497124, -0.03725949445659244, 0.004257572047295569, -0.01222536107992118, 0.0032939646728981638, -0.023231464400571267, 0.010409583738079167, 0.0013675689059239131, 0.01411980072340921, -0.016663199931694486, -0.0004391952994210324, -0.0012258136883719919, -0.032225133228280384, -0.002738415368944635, -0.03314285480332247, -0

In [24]:
import os
import pinecone
from langchain.vectorstores import Pinecone
from pinecone import Pinecone


In [25]:
pc = Pinecone(
    api_key=os.environ.get("PINECONE_API_KEY")
)

In [28]:
pc.delete_index("minecraft")

hasta aquí funciona todo!!!!

In [26]:
index = pc.Index("minecraft")

In [27]:
index.describe_index_stats()

{'dimension': 1536,
 'index_fullness': 0.0,
 'namespaces': {},
 'total_vector_count': 0}

In [ ]:
print(vectores)

In [37]:
!pip install langchain-pinecone

In [42]:
# index.upsert(
#  vectors=[{"id": "A", "values": vectores}]
# )


for i, fragmento in enumerate(fragmentos):
    # Obtener los vectores de embeddings del fragmento
    vectores = embeddings.embed_query(fragmento.page_content)
    index.upsert(
    vectors=[{"id": f"documento_{i+1}", "values": vectores}]
)


### Borrando Index de Pinecone

In [ ]:
import pinecone
from pinecone import Pinecone, PodSpec
pc = Pinecone(api_key="77476dc3-0ee8-47e1-bb5d-91216cb27895")
pc.delete_index("example1")

In [ ]:
pc.create_index(
        name='minecraft',
        dimension=1536,
        metric='cosine',
        spec=PodSpec(
            cloud='gcp',
            region='us-west-2'
        )
    )



TypeError: PodSpec.__new__() got an unexpected keyword argument 'cloud'

### Creando Vectores (Embeddings) y subirlos a (Pinecone)

In [ ]:
def creando_vectores(index_name):
    import pinecone
    from langchain.vectorstores import Pinecone
    from langchain.embeddings.openai import OpenAIEmbeddings

    embeddings = OpenAIEmbeddings()

    pinecone.init(api_key=os.environ.get('77476dc3-0ee8-47e1-bb5d-91216cb27895'))

    if index_name in pinecone.list_indexes():
        print(f'El índice {index_name} ya existe. Cargando los embeddings ... ', end='')
        vectores = Pinecone.from_existing_index(index_name, embeddings)
        print('Ok')
    else:
        print(f'Creando el índice {index_name} y los embeddings ...', end='')
        pinecone.create_index(index_name, dimension=1536, metric='cosine')
        vectores = Pinecone.from_documents(fragmentos, embeddings, index_name=index_name)
        print('Ok')

    return vectores

In [ ]:
pinecone.create_index('minecraft', dimension=1536, metric='cosine')


AttributeError: create_index is no longer a top-level attribute of the pinecone package.

To use create_index, please create a client instance and call the method there instead.

Example:

    from pinecone import Pinecone, ServerlessSpec

    pc = Pinecone(api_key='YOUR_API_KEY')
    pc.create_index(
        name='my-index',
        dimension=1536,
        metric='euclidean',
        spec=ServerlessSpec(
            cloud='aws',
            region='us-west-2'
        )
    )



In [ ]:
vectores = Pinecone.from_documents(fragmentos, embeddings, index_name=index_name)
        print('Ok')

    return vectores

In [ ]:
index_name = 'minecraft'
vectores = creando_vectores(index_name)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.0.9 and will be removed in 0.2.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import OpenAIEmbeddings`.
  warn_deprecated(


AttributeError: init is no longer a top-level attribute of the pinecone package.

Please create an instance of the Pinecone class instead.

Example:

    import os
    from pinecone import Pinecone, ServerlessSpec

    pc = Pinecone(
        api_key=os.environ.get("PINECONE_API_KEY")
    )

    # Now do stuff
    if 'my_index' not in pc.list_indexes().names():
        pc.create_index(
            name='my_index', 
            dimension=1536, 
            metric='euclidean',
            spec=ServerlessSpec(
                cloud='aws',
                region='us-west-2'
            )
        )



### Haciendo consultas

In [ ]:
def consultas(vectores, pregunta):
    from langchain.chains import RetrievalQA
    from langchain.chat_models import ChatOpenAI

    llm = ChatOpenAI(model='gpt-3.5-turbo', temperature=1)

    retriever = vectores.as_retriever(search_type='similarity', search_kwargs={'k': 3})

    chain = RetrievalQA.from_chain_type(llm=llm, chain_type="stuff", retriever=retriever)

    answer = chain.run(pregunta)
    return answer

### Añadiendo memoria

In [ ]:
def consulta_con_memoria(vectores, pregunta, memoria=[]):
    from langchain.chains import ConversationalRetrievalChain
    from langchain.chat_models import ChatOpenAI

    llm = ChatOpenAI(temperature=1)
    retriever = vectores.as_retriever(search_type='similarity', search_kwargs={'k': 3})

    crc = ConversationalRetrievalChain.from_llm(llm, retriever)
    respuesta = crc({'question': pregunta, 'chat_history': memoria})
    memoria.append((pregunta, respuesta['answer']))

    return respuesta, memoria

### Resumen Final

In [ ]:
documento = "minecraft.pdf"
contenido = cargar_documento(documento)
fragmentos = fragmentar(contenido)
print(f"El Número de fragmentos es de: {len(fragmentos)} fragmentos")
costo_embedding(fragmentos)
borrar_indices("todos")
index_name = 'minecraft'
vectores = creando_vectores(index_name)

In [ ]:
memoria = []
while True:
    pregunta = input("Realiza una pregunta escribe 'salir' para terminar: \n")
    if pregunta == "salir":
        print("Adios!!!")
        break
    else:
        respuesta, memoria = consulta_con_memoria(vectores, pregunta, memoria)
        print(respuesta['answer'])


Realiza una pregunta escribe 'salir' para terminar: 
quien es el creador del juego?
El juego Minecraft: Story Mode fue desarrollado por Telltale Games en colaboración con Mojang Studios, la compañía que creó el juego original de Minecraft.
Realiza una pregunta escribe 'salir' para terminar: 
¿Qué me permite hacer el modo espectador?
El modo espectador te permite teletransportarte a otros jugadores en la partida. También te permite ver el juego desde el punto de vista de otro jugador o criatura. En algunos casos, puedes cambiar entre las perspectivas de primera y tercera persona. No hay información específica sobre otras funciones que pueda proporcionar el modo espectador.
